In [16]:
#在 临时文件/赋能答题纸 目录中保留一个pdf(赋能试卷的答题纸), 不留别的pdf文件. 
#在 模板文件 目录中保留 赋能template.txt.
#在 临时文件/赋能答题纸 目录中保留output目录.
"""---设置文件名---"""
filename = "赋能42"

"""---设置题目列表---"""
problems = r"""
746:753,31396,755

"""
#完成后将含有 filename 的文件移至其它目录

import os,re,json,shutil
from PIL import Image


def generate_number_set(string,dict):
    string = re.sub(r"[\n\s]","",string)
    string_list = string.split(",")
    numbers_list = []
    for s in string_list:
        if not ":" in s:
            numbers_list.append(s.zfill(6))
        else:
            start,end = s.split(":")
            for ind in range(int(start),int(end)+1):
                numbers_list.append(str(ind).zfill(6))
    return numbers_list

#读取数据库
with open("../../题库0.3/Problems.json","r",encoding = "utf8") as f:
    jsondata = f.read()
pro_dict = json.loads(jsondata)

#读取pdf文件并转化为png
pdffile = "临时文件/赋能答题纸/"+[f for f in os.listdir("临时文件/赋能答题纸") if ".pdf" in f][0]
try:
    shutil.copy(pdffile,"tempanswersheet.pdf")
except:
    os.remove("tempanswersheet.pdf")
    shutil.copy(pdffile,"tempanswersheet.pdf")
os.system("pdftocairo -png tempanswersheet.pdf")
try:
    os.rename("tempanswersheet-1.png","临时文件/赋能答题纸/output/"+filename+"答题纸.png")
except:
    os.remove("临时文件/赋能答题纸/output/"+filename+"答题纸.png")
    os.rename("tempanswersheet-1.png","临时文件/赋能答题纸/output/"+filename+"答题纸.png")
os.rename(pdffile,"临时文件/赋能答题纸/"+filename+"答题纸_raw.pdf")
os.remove("tempanswersheet.pdf")

#图片下方涂白
pic = Image.open("临时文件/赋能答题纸/output/"+filename+"答题纸.png")
whiteheight = pic.size[1]-880-5
whitewidth = pic.size[0]-100
whitecover = Image.new("RGB",(whitewidth,whiteheight),(255,255,255))
pic1 = pic
pic1.paste(whitecover,(2,880))
pic1.save("临时文件/赋能答题纸/output/"+filename+"答题纸.png")


#替换tex模板中的内容
problem_list = [id for id in generate_number_set(problems.strip(),pro_dict) if id in pro_dict]

with open("模板文件/赋能template.txt","r",encoding="utf8") as f:
    texdata = f.read()
texdata = texdata.replace("背景待替换",filename+"答题纸.png")
data_problems = "\n\n"
for id in problem_list:
    problemset = pro_dict[id]
    problem = problemset["content"]
    data_problems += "\\item " + "{\\tiny ("+id+")} "+problem + "\n\n"
texdata = texdata.replace("题目待替换",data_problems)

with open("临时文件/赋能答题纸/output/"+filename+".tex","w",encoding="utf8") as f:
    f.write(texdata)

#编译文件
os.chdir("临时文件/赋能答题纸/output")
os.system("xelatex -interaction=batchmode " + filename +".tex")
print(os.system("xelatex -interaction=batchmode " +  filename +".tex"))
os.chdir("../../..")

0
